In [19]:
!conda install plotly -y


Solving environment: done

## Package Plan ##

  environment location: /home/paul/anaconda3

  added / updated specs:
    - plotly


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    conda-4.12.0               |   py39h06a4308_0        14.5 MB
    plotly-5.6.0               |     pyhd3eb1b0_0         2.7 MB
    tenacity-8.0.1             |   py39h06a4308_0          33 KB
    ------------------------------------------------------------
                                           Total:        17.2 MB

The following NEW packages will be INSTALLED:

  plotly             pkgs/main/noarch::plotly-5.6.0-pyhd3eb1b0_0
  tenacity           pkgs/main/linux-64::tenacity-8.0.1-py39h06a4308_0

The following packages will be UPDATED:

  conda                               4.11.0-py39h06a4308_0 --> 4.12.0-py39h06a4308_0



plotly-5.6.0         | 2.7 MB    | ##################################### | 100% 
te

In [20]:
import pandas as pd
import plotly.express as px
#from fuzzywuzzy import fuzz
#from wordcloud import WordCloud
import numpy as np
import matplotlib.pyplot as plt
#from PIL import Image

In [ ]:
class tidy_df():
    def __init__(self):
        self.indices = None
        self.values = list()
        
    
    def set_indices(self, 
                    df: pd.DataFrame, 
                    col_locs: tuple, 
                    header_row: int) -> None:
        
        start, end = col_locs
        ind_df = df.iloc[header_row+1:,start:end+1]
        print(ind_df.columns)
        ind_df.columns = df.iloc[header_row,start:end+1]
        ind_df.reset_index(inplace=True, drop=True)
        self.indices = ind_df
        return None
 
    def set_values(self, df: pd.DataFrame, header_row: int, 
                   col_start: int, col_width: int, coverage_type: str) -> None:
        
        col_names = list(df.iloc[header_row+1,col_start:col_start + col_width])
        print(col_names)
        i = col_start
        
        
        
        while i < len(df.columns) - col_start:
            
            temp_df = df.iloc[header_row+2:, i:i+col_width]
            temp_df.columns = col_names
            
            temp_df.reset_index(inplace=True, drop=True)
            joined_df = pd.concat([self.indices, temp_df], axis=1)
            joined_df['year'] = df.iloc[header_row,i]
            joined_df['coverage_type'] = coverage_type.lower()
            
            self.values.append(joined_df)
            i += col_width
        return None

    def glue(self):
        tidier_df = pd.concat(self.values, ignore_index=True, axis=0)
        return tidier_df

In [ ]:
filename1 = "data/DSD_MCD_R21_DYT20_Web.xlsx"
filename2 = "data/DSD_MCD_R17_DYT16_Web.xlsx"
filename3 = "data/DSD_PTD_R21_DYT20_Web.xlsx"
filename4 = "data/DSD_PTD_R17_DYT16_Web.xlsx"

mcd_costs_20 = pd.read_excel(filename1, sheet_name=1, skiprows=1).iloc[:,:-2]
mcd_costs_16 = pd.read_excel(filename2, sheet_name=1, skiprows=1).iloc[:,:-2]
mcr_costs_20 = pd.read_excel(filename3, sheet_name=1, skiprows=1).iloc[:,:-2]
mcr_costs_16 = pd.read_excel(filename4, sheet_name=1, skiprows=1).iloc[:,:-2]
    
dataframe_dict = {"medicaid": [mcd_costs_16, mcd_costs_20], "medicare": [mcr_costs_16, mcr_costs_20]}

tidy = tidy_df()

tidy.set_indices(mcd_costs_20, (0,2), 1)
tidy.set_values(mcd_costs_20, 0, 3, 6, 'medicaid')
    
tidy.set_indices(mcd_costs_16, (0,2), 1)
tidy.set_values(mcd_costs_16, 0, 3, 5, 'medicaid')

tidy.set_indices(mcr_costs_20, (0,2), 1)
tidy.set_values(mcr_costs_20, 0, 3, 8, 'medicare')

tidy.set_indices(mcr_costs_16, (0,2), 1)
tidy.set_values(mcr_costs_16, 0, 3, 7, 'medicare')



In [ ]:
new_list = []
cols_to_keep = ['Brand Name', 
                'Generic Name', 
                'Number of Manufacturers',
                'Total Spending', 
                'Total Dosage Units', 
                'Total Claims',
                'Average Spending Per Dosage Unit (Weighted)',
                'Average Spending Per Claim',
                'year', 
                'coverage_type']
for df in tidy.values:
    if 'Average \nSpending Per Claim' in df.columns:
        print("found it")
        df['Average Spending Per Claim'] = df['Average \nSpending Per Claim']
    print(df.columns)
    
    new_list.append(df[cols_to_keep])

tidy.values = new_list

In [ ]:
cleaned_df = tidy.glue()
cleaned_df['year'] = cleaned_df['year'].apply(lambda x: int(x[-4:]))

In [ ]:
cleaned_df[cleaned_df['Brand Name']=='Zytiga']

In [ ]:
drug_info = pd.read_excel(filename1, sheet_name=3, skiprows=4, header=0)

In [ ]:
drug_info.loc[5]

In [ ]:
def get_drug_info(search_str: str):
    words = list()
    for row in drug_info.iterrows():
        rat = fuzz.partial_ratio(search_str, str(row[1][1]))
        if rat >=75:
            words.append(row[1][2])
    return words
        

In [ ]:
def display_img(img):
    fig = plt.figure(figsize=(12,10))
    ax = fig.add_subplot(111)
    ax.imshow(img,cmap='gray', vmin=0, vmax=1)
    
bottle = np.zeros((600,600),dtype=np.int8)

bottle[100:200,150:450]=1
bottle[100:550, 175:425]=1

display_img(bottle)

In [ ]:
import time
time.gmtime(time.time())

In [ ]:

filename1 = "data/DSD_PTD_R21_DYT20_Web.xlsx"
filename2 = "data/DSD_MCD_R21_DYT20_Web.xlsx"


drug_info_mcr = pd.read_excel(filename1, sheet_name=3, skiprows=4, header=0)

drug_info_mcd = pd.read_excel(filename2, sheet_name=3, skiprows=4, header=0)

print(drug_info_mcr.columns)
print(drug_info_mcd.columns)


In [7]:
data = pd.read_csv('./data/cleaned.csv', header=0, index_col=0)

In [8]:
medicare = data[data['coverage_type']=='medicare']

In [10]:
medicaid = data[data['coverage_type']=='medicaid']

In [14]:
# a test?
assert len(medicaid) + len(medicare) == len(data)

In [22]:
?px.histogram

In [30]:
px.box(medicaid, x='year', y='Total Spending', hover_name='Brand Name')

In [41]:
px.scatter(medicare, x='Average Spending Per Dosage Unit (Weighted)',
                      y='Average Spending Per Claim', hover_name='Brand Name', facet_col='year', facet_col_wrap=3)